### Imports

In [91]:
import matplotlib.pyplot as plt
import numpy as np
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
from IPython.display import display, HTML
from matplotlib.cm import plasma
from matplotlib.colors import Normalize

from src.rft_main import *


### Inputs

In [92]:
### INPUTS ###
inputs = {
    "model": "CPT_DIA_LCPC",
    "bulk_density": 1638,
    "friction_material": 0.72,
    "friction_surface": 0.4,
    "friction_type": "coefficient",
    "gravity": 9.81 * 70,
    "linear_velocity": 0.1,
    "direction_angle_xz_deg": -90,
    "direction_angle_y_deg": -90,
    "rotation": False,
    "angular_velocity": np.array([0, 0, -1 * np.pi]),
    "start_depth": 0,
    "end_depth": 300,
    "step_size": 30,
}
colormap = "Plasma"


In [93]:
results = run_rft(**inputs)

point_list = results["point_list"]
normal_list = results["normal_list"]
area_list = results["area_list"]
depth_list = results["depth_list"]
object_width_x = results["object_width_x"]
object_width_y = results["object_width_y"]
object_height = results["object_height"]
vertices = results["vertices"]
faces = results["faces"]
trg = results["trg"]
movement = results["movement"]
z_local = results["z_local"]
r_local = results["r_local"]
theta_local = results["theta_local"]
alpha_generic = results["alpha_generic"]
alpha_generic_n = results["alpha_generic_n"]
alpha_generic_t = results["alpha_generic_t"]
alpha = results["alpha"]
depth = results["depth"]
forces = results["forces"]
pressures = results["pressures"]
force_x = results["force_x"]
force_y = results["force_y"]
force_z = results["force_z"]
resultant = results["resultant"]
torques = results["torques"]
torque_x = results["torque_x"]
torque_y = results["torque_y"]
torque_z = results["torque_z"]
resultant_torque = results["resultant_torque"]
result_matrix = results["result_matrix"]

path = (
    f"{inputs['model']}_"
    f"{inputs['bulk_density']}_"
    f"{inputs['friction_material']}_"
    f"{inputs['friction_surface']}_"
    f"{inputs['direction_angle_xz_deg']}_"
    f"{inputs['direction_angle_y_deg']}_"
    f"{'rotating' if inputs['rotation'] else 'static'}_"
    f"{inputs['angular_velocity'][2]:.2f}rad_"  # Formats to 2 decimal places with 'rad' suffix
    f"{inputs['start_depth']}_"
    f"{inputs['end_depth']}"
)


html_content = f"""
<div style="
    background-color: #1f2c56;
    padding: 20px;
    border-radius: 10px;
    font-family: 'Helvetica Neue', Helvetica, Arial, sans-serif;
    text-align: center;
    color: #abbbc9;
    box-shadow: 0 4px 8px rgba(0, 0, 0, 0.2);
    margin: 10px 0;
">
    <h2 style="
        font-size: 24px;
        margin-bottom: 15px;
        font-weight: 300;
        letter-spacing: 1px;
        color: #4ecdc4;
    ">Results</h2>
    <div style="
        font-size: 18px;
        margin: 10px 0;
    "><strong style="color: #ff6b6b;">Force X:</strong> {force_x:.2f} N</div>
    <div style="
        font-size: 18px;
        margin: 10px 0;
    "><strong style="color: #ff6b6b;">Force Y:</strong> {force_y:.2f} N</div>
    <div style="
        font-size: 18px;
        margin: 10px 0;
    "><strong style="color: #ff6b6b;">Force Z:</strong> {force_z:.2f} N</div>
</div>
"""
display(HTML(html_content))


Processed movement from 0 to 210 mm


In [94]:
%%html
<style>
.cell-output-ipywidget-background {
   background-color: transparent !important;
}
.jp-OutputArea-output {
   background-color: transparent;
}
</style>


# Plots

## 3D Mesh

In [95]:
# Creating a 3D plot using Plotly
fig = go.FigureWidget()


fig.add_trace(
    go.Mesh3d(
        x=vertices[:, 0],
        y=vertices[:, 1],
        z=vertices[:, 2],
        i=faces[:, 0],
        j=faces[:, 1],
        k=faces[:, 2],
        colorscale=colormap,
        showscale=False,
        intensity=vertices[:, 2],
        cmin=np.min(vertices[:, 2]),
        cmax=np.max(vertices[:, 2]),
    )
)

# Updating the layout of the plot
fig.update_layout(
    width=600,
    height=500,
    margin=dict(l=10, r=10, t=10, b=10),
    scene=dict(
        aspectmode="data",
        aspectratio=dict(
            x=np.ptp(point_list[:, 0]),
            y=np.ptp(point_list[:, 1]),
            z=np.ptp(point_list[:, 2]),
        ),
        camera=dict(eye=dict(x=1.75, y=1.5, z=1.25)),
    ),
)

fig.write_image("plots/surface_" + path + ".svg")
display(fig)


FigureWidget({
    'data': [{'cmax': 10.392304,
              'cmin': 0.0,
              'colorscale': [[0.0, '#0d0887'], [0.1111111111111111, '#46039f'],
                             [0.2222222222222222, '#7201a8'], [0.3333333333333333,
                             '#9c179e'], [0.4444444444444444, '#bd3786'],
                             [0.5555555555555556, '#d8576b'], [0.6666666666666666,
                             '#ed7953'], [0.7777777777777778, '#fb9f3a'],
                             [0.8888888888888888, '#fdca26'], [1.0, '#f0f921']],
              'i': array([   2,    0,    0, ..., 1214, 1213,  999], dtype=int64),
              'intensity': array([10.392304, 10.392304, 10.392304, ..., 10.392304, 10.392304, 10.392304],
                                 dtype=float32),
              'j': array([ 11,  11,   7, ..., 999, 999, 813], dtype=int64),
              'k': array([   0,    7,    1, ..., 1213,  998,  998], dtype=int64),
              'showscale': False,
              'type':

## Movement

In [96]:
fig = go.FigureWidget()
fig.add_trace(
    go.Cone(
        x=point_list[:, 0],
        y=point_list[:, 1],
        z=point_list[:, 2],
        u=movement[:, 0],
        v=movement[:, 1],
        w=movement[:, 2],
        sizeref=50,
        showscale=False,
    )
)

# Updating the layout of the plot
fig.update_layout(
    width=600,
    height=500,
    margin=dict(l=10, r=10, t=10, b=10),
    scene=dict(
        aspectmode="data",
        aspectratio=dict(
            x=np.ptp(point_list[:, 0]),
            y=np.ptp(point_list[:, 1]),
            z=np.ptp(point_list[:, 2]),
        ),
        camera=dict(eye=dict(x=1.75, y=1.5, z=1.25)),
    ),
)

fig.write_image("plots/movement_" + path + ".svg")
display(fig)


FigureWidget({
    'data': [{'showscale': False,
              'sizeref': 50,
              'type': 'cone',
              'u': array([0., 0., 0., ..., 0., 0., 0.]),
              'uid': '0048c38c-410a-4b5b-a332-206e5bafc208',
              'v': array([0., 0., 0., ..., 0., 0., 0.]),
              'w': array([-1., -1., -1., ..., -1., -1., -1.]),
              'x': array([-5.92973   , -5.8711762 , -5.933553  , ..., -0.24987666,  0.05672081,
                           0.07022575], dtype=float32),
              'y': array([ 0.24723768,  0.12165663, -0.12558104, ...,  0.00392441,  0.11132085,
                          -0.10333406], dtype=float32),
              'z': array([-199.93245, -200.04071, -199.93245, ..., -209.7835 , -210.     ,
                          -210.     ], dtype=float32)}],
    'layout': {'height': 500,
               'margin': {'b': 10, 'l': 10, 'r': 10, 't': 10},
               'scene': {'aspectmode': 'data',
                         'aspectratio': {'x': 11.867106, 'y': 

## Force Quiver

In [97]:
# Calculating the endpoints and the magnitudes of the vectors
endpoints = point_list - forces * 200
magnitudes = np.linalg.norm(forces, axis=1)
# Normalize the magnitudes to the range [0, 1]
norm = Normalize()
normalized_magnitudes = norm(magnitudes)
# Get colors from a colormap
colors = plasma(normalized_magnitudes)

# Preparing data for plot
x_lines = np.c_[
    point_list[:, 0], endpoints[:, 0], np.full(len(point_list), np.nan)
].flatten()
y_lines = np.c_[
    point_list[:, 1], endpoints[:, 1], np.full(len(point_list), np.nan)
].flatten()
z_lines = np.c_[
    point_list[:, 2], endpoints[:, 2], np.full(len(point_list), np.nan)
].flatten()

# Flatten the colors array and convert to RGB strings
colors = (colors[:, :3] * 255).astype(int)
color_strings = [f"rgb({r},{g},{b})" for r, g, b in colors]
color_strings = np.repeat(
    color_strings, 3
)  # Repeat for each segment of the line (start, end, break)

# Creating a 3D plot using Plotly
line_marker = dict(width=5, color=color_strings)
fig = go.FigureWidget(
    data=[go.Scatter3d(x=x_lines, y=y_lines, z=z_lines, mode="lines", line=line_marker)]
)

# Updating the layout of the plot
fig.update_layout(
    width=600,
    height=500,
    margin=dict(l=10, r=10, t=10, b=10),
    scene=dict(
        aspectmode="data",
        aspectratio=dict(x=1, y=1, z=1),
        camera=dict(eye=dict(x=1.75, y=1.5, z=1.25)),
    ),
)

# Show the plot
fig.write_image("plots/quiver_" + path + ".svg")
display(fig)


FigureWidget({
    'data': [{'line': {'color': array(['rgb(239,248,33)', 'rgb(239,248,33)', 'rgb(239,248,33)', ...,
                                       'rgb(12,7,134)', 'rgb(12,7,134)', 'rgb(12,7,134)'], dtype=object),
                       'width': 5},
              'mode': 'lines',
              'type': 'scatter3d',
              'uid': 'a3392c79-d1bb-4ca3-8fb3-b56273c7599d',
              'x': array([-5.92972994e+00, -2.11036318e+02,             nan, ...,  7.02257529e-02,
                           3.85622328e+00,             nan]),
              'y': array([ 0.24723768,  6.69310143,         nan, ..., -0.10333406, -5.67426652,
                                  nan]),
              'z': array([-199.93244934, -460.60363857,           nan, ..., -210.        ,
                          -218.55615486,           nan])}],
    'layout': {'height': 500,
               'margin': {'b': 10, 'l': 10, 'r': 10, 't': 10},
               'scene': {'aspectmode': 'data',
                         '

## Force Scatter

In [98]:
magnitudes = np.linalg.norm(pressures, axis=1)

fig = go.Figure()

scatter = go.Scatter3d(
    x=point_list[:, 0],
    y=point_list[:, 1],
    z=point_list[:, 2],
    mode="markers",
    marker=dict(
        size=2,
        color=magnitudes,  # Set color equal to a variable
        colorscale=colormap,  # Choose a colormap
        colorbar=dict(
            title="Pressure [N/mm²]",
            len=0.75,
            thickness=20,
        ),
        opacity=1,
    ),
)

fig.add_trace(scatter)

# Update the layout if needed
fig.update_layout(
    width=700,
    height=500,
    margin=dict(l=10, r=10, t=10, b=10),
    scene=dict(
        aspectmode="data",
        aspectratio=dict(x=1, y=1, z=1),
        camera=dict(eye=dict(x=2, y=2, z=1.5)),
    ),
)

# Show the plot
fig.write_image("plots/scatter_" + path + ".svg")
display(fig)


## Force Scatter XYZ

In [99]:
# Calculate global color scale limits based on the maximum absolute pressure value
max_abs_pressure = np.max(np.abs(pressures))

fig = make_subplots(
    rows=1,
    cols=3,
    subplot_titles=("X", "Y", "Z"),
    specs=[[{"type": "scatter3d"}, {"type": "scatter3d"}, {"type": "scatter3d"}]],
)

for i in range(3):
    scatter = go.Scatter3d(
        x=point_list[:, 0],
        y=point_list[:, 1],
        z=point_list[:, 2],
        mode="markers",
        marker=dict(
            size=1,
            color=np.abs(pressures[:, i]),  # Set color equal to a variable
            colorscale=colormap,  # Choose a colormap
            cmin=0,  # Set consistent color scale limits
            cmax=max_abs_pressure,  # Set consistent color scale limits
            colorbar=dict(
                title="Pressure [N/mm²]",
                len=0.75,
                thickness=20,
            ),
            opacity=1,
        ),
    )
    fig.add_trace(scatter, row=1, col=i + 1)

fig.update_layout(
    width=1200,  # Adjusted for 3 plots
    height=500,
    margin=dict(l=10, r=10, t=30, b=10),
    scene1=dict(
        aspectmode="data",
        aspectratio=dict(x=1, y=1, z=1),
        camera=dict(eye=dict(x=3, y=3, z=2)),
    ),
    scene2=dict(
        aspectmode="data",
        aspectratio=dict(x=1, y=1, z=1),
        camera=dict(eye=dict(x=3, y=3, z=2)),
    ),
    scene3=dict(
        aspectmode="data",
        aspectratio=dict(x=1, y=1, z=1),
        camera=dict(eye=dict(x=3, y=3, z=2)),
    ),
    showlegend=False,
)

fig.write_image("plots/scatterxyz_" + path + ".svg")
display(fig)


In [100]:
fig = make_subplots(
    rows=2,
    cols=3,
    subplot_titles=("X", "Y", "Z"),
    shared_xaxes=True,
    shared_yaxes=True,
    vertical_spacing=0.05,
    horizontal_spacing=0.05,
)

x_axis_range = [
    np.min(result_matrix[:, 0]),
    np.max(result_matrix[:, 0]),
]
y_axis_range = [
    np.min(result_matrix[:, 1:4]) - np.ptp(result_matrix[:, 1:4]) * 0.1,
    np.max(result_matrix[:, 1:4]) + np.ptp(result_matrix[:, 1:4]) * 0.1,
]

for i in range(3):
    scatter = go.Scatter(
        x=result_matrix[:, 0],
        y=result_matrix[:, i + 1],
        line_shape="spline",
        line=dict(color="slateblue", width=2),
    )
    fig.add_trace(scatter, row=1, col=i + 1)
    fig.update_xaxes(range=x_axis_range, row=1, col=i + 1)
    fig.update_yaxes(range=y_axis_range, row=1, col=i + 1)
    fig.update_yaxes(title_text="Force [N]", row=1, col=1)

y_axis_range = [
    np.min(result_matrix[:, 4:8]) - np.ptp(result_matrix[:, 4:8]) * 0.1,
    np.max(result_matrix[:, 4:8]) + np.ptp(result_matrix[:, 4:8]) * 0.1,
]

for i in range(3):
    scatter = go.Scatter(
        x=result_matrix[:, 0],
        y=result_matrix[:, i + 4],
        line_shape="spline",
        line=dict(color="teal", width=2),
    )
    fig.add_trace(scatter, row=2, col=i + 1)
    fig.update_xaxes(range=x_axis_range, row=2, col=i + 1, title_text="Depth [mm]")
    fig.update_yaxes(range=y_axis_range, row=2, col=i + 1)
    fig.update_yaxes(title_text="Torque [Nm]", row=2, col=1)

fig.update_layout(
    width=1200,  # Adjusted for 6 plots
    height=600,
    margin=dict(l=10, r=10, t=30, b=10),
    showlegend=False,
)

fig.write_image("plots/graphs_" + path + ".svg")
display(fig)


In [101]:
# print point nr 1666 (row in point list)
print("point =", point_list[1666])
print("normal =", normal_list[1666])
print("area =", area_list[1666])
print("movement =", movement[1666])
print("depth =", depth_list[1666])
print("z_local =", z_local[1666])
print("r_local =", r_local[1666])
print("theta_local =", theta_local[1666])
print("alpha_generic =", alpha_generic[1666])
print("alpha_generic_n =", alpha_generic_n[1666])
print("alpha_generic_t =", alpha_generic_t[1666])
print("alpha =", alpha[1666])
print("force =", forces[1666])
print("pressure =", pressures[1666])


point = [  -2.559384     3.8498433 -202.20576  ]
normal = [-0.4868385   0.7163614  -0.49981475]
area = [0.0552074]
movement = [ 0.  0. -1.]
depth = [-202.20576]
z_local = [0 0 1]
r_local = [-0.56208321  0.82708069  0.        ]
theta_local = [-0.82708069 -0.56208321  0.        ]
alpha_generic = [ 0.11509096 -0.16935128  0.63095162]
alpha_generic_n = [ 0.23986842 -0.35295582  0.2462619 ]
alpha_generic_t = [-0.12477746  0.18360454  0.38468972]
alpha = [ 0.04082009 -0.06006496  0.09225125]
force = [ 0.45568502 -0.67052045  1.02982412]
pressure = [  8.25405724 -12.14548183  18.65373409]
